# Validation returns
Aquí se obtienen los retornos ed los algoritmos entrenados sobre los retornos de validación.

In [1]:
import sys
import os
import pandas as pd

# Añadir el directorio raíz del proyecto al PYTHONPATH
project_root = os.path.abspath(os.path.join(os.getcwd(), '..'))
sys.path.append(project_root)


from stock_trading_env.trading_env import TradingEnv
import gymnasium as gym

import matplotlib.pyplot as plt

from stable_baselines3 import PPO

In [2]:
gym.envs.register(
    id='TradingEnv-v0',
    entry_point='stock_trading_env.trading_env:TradingEnv',
)

### Helper functions

In [3]:
def model_predict(rf_model, val_data):

    environ = gym.make(
        "TradingEnv-v0",
        name="BTCUSD",
        df=val_data,
        windows=10,
        positions=[-1, 0, 1],  # -1 (=SHORT), +1 (=LONG)
        initial_position=0,  # Initial position
        trading_fees=0.01 / 100,  # 0.01% per stock buy/sell
        #reward_function=reward_function,
        portfolio_initial_value=100_000,  # in FIAT (here, USD)
        max_episode_duration='max',
        )
    

    try:
        obs, info = environ.reset()
        done = False

        obs_list = []
        reward_list = []
        info_list = []
        action_list = []
        real_action_taken_list = []

        while not done:
            # Predice la acción usando el modelo entrenado
            action, _states = rf_model.predict(obs)
            
            # Toma la acción en el entorno
            obs, reward, done, truncated, info = environ.step(action)

            action_list.append(action)
            real_action_taken_list.append(info['real_action_taken'])
            obs_list.append(obs)
            reward_list.append(reward)
            info_list.append(info)
    except Exception as ex:
        pass
    finally:
        return obs_list, reward_list, info_list, action_list, real_action_taken_list

In [4]:
def calculate_returns(data:pd.DataFrame, action_name: str):
    # Inicializar variables para trackear la posición y el cash
    position = 0
    cash = 0

    # Lista para almacenar los retornos de la estrategia
    returns = []
    

    for i in range(1, len(data)):
        
        action = data.loc[i,action_name]
        #real_action = fixed_validation_data.loc[i, 'real_actions_taken']
        price = data.loc[i, 'close']
        prev_price = data.loc[i-1, 'close']
        
        # Comprar
        if action == 1:  
            # Actualizar posición (por simplicidad, se asume compra completa)
            position += 1
            cash -= price

            # No hay retorno inmediato al comprar
            returns.append(0)  
            
        
        # Vender
        elif action == -1:  
            # Vender solo si tienes activo
            if position > 0:  
                returns.append((price - prev_price) / prev_price)  # Retorno de la venta
                cash += price
                position -= 1
            else:
                returns.append(0)  # Si no puedes vender, el retorno es 0
                
        
        # Mantener
        else: 
            if position > 0:  # Si tienes posición, registrar retorno
                returns.append((price - prev_price) / prev_price)
                
            else:
                returns.append(0)  # Si no tienes posición, el retorno es 0
        

    # el primer retorno es nan, asique lo sustituyo por 0.
    returns.insert(0, 0)

    return pd.Series([float(num) for num in returns])



# BTC original

In [25]:
# Cargar el modelo entrenado
BTC_original_model = PPO.load("ppo_BTC_original.zip")

In [26]:
BTC_ORIG_VAL_DATA = pd.read_parquet(r'C:\Users\adelapuente\Desktop\math_tfm\02_training_data\BTC_original_processed_out_of_sample.parquet')

In [27]:
btc_orig_obs, btc_orig_rewards, btc_orig_infos, btc_orig_actions, btc_orig_real_action_taken = model_predict(BTC_original_model, BTC_ORIG_VAL_DATA)

SELLING --> 	price:42338.89 | 	profit: 84677.78 | port: 99990.36 | port-1: 100000.00
BUYING --> 	price:42351.94 | 	cost: 84703.88 | port: 99990.36 | port-1: 99990.36
SELLING --> 	price:42346.04 | 	profit: 84692.08 | port: 99978.56 | port-1: 99990.36
BUYING --> 	price:42336.70 | 	cost: 84673.40 | port: 99978.56 | port-1: 99978.56
SELLING --> 	price:42337.00 | 	profit: 84674.00 | port: 99979.16 | port-1: 99973.24
BUYING --> 	price:42332.91 | 	cost: 84665.82 | port: 99979.16 | port-1: 99979.16
SELLING --> 	price:42297.23 | 	profit: 84594.46 | port: 99907.80 | port-1: 99923.18
BUYING --> 	price:42280.06 | 	cost: 84560.12 | port: 99907.80 | port-1: 99907.80
SELLING --> 	price:42293.06 | 	profit: 84586.12 | port: 99933.80 | port-1: 99911.72
BUYING --> 	price:42282.14 | 	cost: 84564.28 | port: 99933.80 | port-1: 99933.80
SELLING --> 	price:42231.48 | 	profit: 84462.96 | port: 99832.48 | port-1: 99809.04
BUYING --> 	price:42240.30 | 	cost: 84480.60 | port: 99832.48 | port-1: 99832.48
SELLING -

In [28]:
btc_orig_infos[0]

{'idx': 10,
 'step': 1,
 'date': 3155050,
 'agent_action': -1,
 'real_action_taken': 0,
 'portfolio_exposition': 0.0,
 'data_close': 42343.71,
 'data_date': Timestamp('2024-01-01 00:10:00'),
 'portfolio_valuation': 100000.0,
 'portfolio_distribution_asset': 0,
 'portfolio_distribution_cash': 100000.0,
 'reward': -0.01,
 'strategy_returns': 0.0,
 'stock_price': 42343.71}

Hay que poner todo en orden. La primera muestra es en Timestamp('2024-01-01 00:10:00')
por tanto me cojo la anterior como la primera, y a las acciones tomadas les agrego un "hold" al inicio

In [29]:
btc_orig_val_data_subset = BTC_ORIG_VAL_DATA[['date', 'close']][9:].copy()
# calculo los retornos del benchmark

btc_orig_val_data_subset['BTC Buy&Hold'] = BTC_ORIG_VAL_DATA['close'].pct_change()
btc_orig_val_data_subset.reset_index(inplace=True, drop=True)
btc_orig_val_data_subset

date     close  BTC Buy&Hold
0      2024-01-01 00:09:00  42332.27     -0.000161
1      2024-01-01 00:10:00  42343.71      0.000270
2      2024-01-01 00:11:00  42338.89     -0.000114
3      2024-01-01 00:12:00  42335.78     -0.000073
4      2024-01-01 00:13:00  42328.52     -0.000171
...                    ...       ...           ...
262066 2024-06-30 23:55:00  63394.28      0.000144
262067 2024-06-30 23:56:00  63370.03     -0.000383
262068 2024-06-30 23:57:00  63338.69     -0.000495
262069 2024-06-30 23:58:00  63362.18      0.000371
262070 2024-06-30 23:59:00  63369.30      0.000112

[262071 rows x 3 columns]

In [30]:
len(btc_orig_val_data_subset), len(btc_orig_real_action_taken)

(262071, 262070)

In [31]:
# las acciones predichas directamente las tengo que mapear
action_mapping = [-1, 0, 1]
mapped_actions = [action_mapping[index] for index in btc_orig_actions]

predicted_actions_fixed = [0]
real_actions_fixed = [0]
predicted_actions_fixed.extend(mapped_actions)
real_actions_fixed.extend(btc_orig_real_action_taken)


btc_orig_val_data_subset['predicted_actions'] = predicted_actions_fixed
btc_orig_val_data_subset['real_actions_taken'] = real_actions_fixed

Ahora tengo que convertir las acciones a retornos. Para eso, "filtro" las acciones para que solo se compre o venda en función de si tengo activo o no.
QUE NO SE SI ESTO ESTA BIEN. podria seguir comprando o seguir vendiendo. pero bueno.

In [32]:
btc_orig_val_data_subset['BTC_pred_actions_returns'] = calculate_returns(btc_orig_val_data_subset,'predicted_actions')
btc_orig_val_data_subset['BTC_real_actions_returns'] = calculate_returns(btc_orig_val_data_subset,'real_actions_taken')

In [33]:
btc_orig_val_data_subset.to_parquet('../04_testing/BTC_original_returns.parquet')

# BTC Volumen

In [52]:
# Cargar el modelo entrenado
BTC_volume_model = PPO.load("ppo_BTC_volume.zip")

In [53]:
BTC_VOLUME_VAL_DATA = pd.read_parquet(r'C:\Users\adelapuente\Desktop\math_tfm\02_training_data\BTC_volume_processed_out_of_sample.parquet')

In [54]:
btc_volume_obs, btc_volume_rewards, btc_volume_infos, btc_volume_actions, btc_volume_real_action_taken = model_predict(BTC_volume_model, BTC_VOLUME_VAL_DATA)

BUYING --> 	price:44140.83 | 	cost: 88281.66 | port: 100000.00 | port-1: 100000.00
SELLING --> 	price:44398.97 | 	profit: 88797.94 | port: 100516.28 | port-1: 100177.48
BUYING --> 	price:44435.13 | 	cost: 88870.26 | port: 100516.28 | port-1: 100516.28
SELLING --> 	price:44546.41 | 	profit: 89092.82 | port: 100738.84 | port-1: 100516.28
BUYING --> 	price:44654.40 | 	cost: 89308.80 | port: 100738.84 | port-1: 100738.84
SELLING --> 	price:44691.13 | 	profit: 89382.26 | port: 100812.30 | port-1: 100738.84
BUYING --> 	price:44747.80 | 	cost: 89495.60 | port: 100812.30 | port-1: 100812.30
SELLING --> 	price:44921.18 | 	profit: 89842.36 | port: 101159.06 | port-1: 100812.30
BUYING --> 	price:45072.79 | 	cost: 90145.58 | port: 101159.06 | port-1: 101159.06
SELLING --> 	price:45045.00 | 	profit: 90090.00 | port: 101103.48 | port-1: 101159.06
BUYING --> 	price:44947.91 | 	cost: 89895.82 | port: 101103.48 | port-1: 101103.48
SELLING --> 	price:44883.20 | 	profit: 89766.40 | port: 100974.06 | port

In [55]:
btc_volume_infos[0]

{'idx': 10,
 'step': 1,
 'date': 99160,
 'agent_action': -1,
 'real_action_taken': 0,
 'portfolio_exposition': 0.0,
 'data_close': 43572.71,
 'data_date': Timestamp('2024-01-01 16:37:00'),
 'portfolio_valuation': 100000.0,
 'portfolio_distribution_asset': 0,
 'portfolio_distribution_cash': 100000.0,
 'reward': -0.01,
 'strategy_returns': 0.0,
 'stock_price': 43572.71}

In [56]:
btc_volume_val_data_subset = BTC_VOLUME_VAL_DATA[['date', 'close']][9:].copy()
# calculo los retornos del benchmark

btc_volume_val_data_subset['BTC Buy&Hold'] = BTC_VOLUME_VAL_DATA['close'].pct_change()
btc_volume_val_data_subset.reset_index(inplace=True, drop=True)
btc_volume_val_data_subset

date     close  BTC Buy&Hold
0     2024-01-01 15:13:00  43757.39      0.005269
1     2024-01-01 16:37:00  43572.71     -0.004221
2     2024-01-01 18:04:00  43720.64      0.003395
3     2024-01-01 18:26:00  43911.50      0.004365
4     2024-01-01 18:28:00  43988.00      0.001742
...                   ...       ...           ...
11609 2024-06-30 14:57:00  61974.68      0.008201
11610 2024-06-30 15:59:00  61929.29     -0.000732
11611 2024-06-30 18:19:00  62122.73      0.003124
11612 2024-06-30 18:26:00  62500.00      0.006073
11613 2024-06-30 18:28:00  62770.60      0.004330

[11614 rows x 3 columns]

In [57]:
len(btc_volume_val_data_subset), len(btc_volume_real_action_taken)

(11614, 11613)

In [58]:
# las acciones predichas directamente las tengo que mapear
action_mapping = [-1, 0, 1]
mapped_actions = [action_mapping[index] for index in btc_volume_actions]

predicted_actions_fixed = [0]
real_actions_fixed = [0]
predicted_actions_fixed.extend(mapped_actions)
real_actions_fixed.extend(btc_volume_real_action_taken)

btc_volume_val_data_subset['predicted_actions'] = predicted_actions_fixed
btc_volume_val_data_subset['real_actions_taken'] = real_actions_fixed

In [59]:
btc_volume_val_data_subset['BTC_pred_actions_returns'] = calculate_returns(btc_volume_val_data_subset,'predicted_actions')
btc_volume_val_data_subset['BTC_real_actions_returns'] = calculate_returns(btc_volume_val_data_subset,'real_actions_taken')

In [60]:
btc_volume_val_data_subset.to_parquet('../04_testing/BTC_volume_returns.parquet')

# BTC Dollar

In [43]:
# Cargar el modelo entrenado
BTC_dollar_model = PPO.load("ppo_BTC_dollar.zip")

In [44]:
BTC_DOLLAR_VAL_DATA = pd.read_parquet(r'C:\Users\adelapuente\Desktop\math_tfm\02_training_data\BTC_dollar_processed_out_of_sample.parquet')

In [45]:
btc_dollar_obs, btc_dollar_rewards, btc_dollar_infos, btc_dollar_actions, btc_dollar_real_action_taken = model_predict(BTC_dollar_model, BTC_DOLLAR_VAL_DATA)

BUYING --> 	price:42344.41 | 	cost: 84688.82 | port: 100107.82 | port-1: 100107.82
SELLING --> 	price:42386.13 | 	profit: 84772.26 | port: 100191.26 | port-1: 100193.04
BUYING --> 	price:42381.23 | 	cost: 84762.46 | port: 100191.26 | port-1: 100191.26
SELLING --> 	price:42456.02 | 	profit: 84912.04 | port: 100340.84 | port-1: 100252.96
BUYING --> 	price:42480.00 | 	cost: 84960.00 | port: 100340.84 | port-1: 100340.84
SELLING --> 	price:42455.87 | 	profit: 84911.74 | port: 100292.58 | port-1: 100340.84
BUYING --> 	price:42456.26 | 	cost: 84912.52 | port: 100292.58 | port-1: 100292.58
SELLING --> 	price:42470.99 | 	profit: 84941.98 | port: 100322.04 | port-1: 100363.12
BUYING --> 	price:42494.19 | 	cost: 84988.38 | port: 100322.04 | port-1: 100322.04
SELLING --> 	price:42464.19 | 	profit: 84928.38 | port: 100262.04 | port-1: 100291.80
BUYING --> 	price:42469.69 | 	cost: 84939.38 | port: 100262.04 | port-1: 100262.04
SELLING --> 	price:42474.77 | 	profit: 84949.54 | port: 100272.20 | port

In [46]:
btc_dollar_infos[0]

{'idx': 10,
 'step': 1,
 'date': 843794,
 'agent_action': 1,
 'real_action_taken': 1,
 'portfolio_exposition': 0.8456452,
 'data_close': 42336.17,
 'data_date': Timestamp('2024-01-01 01:18:00'),
 'portfolio_valuation': 100107.81999999999,
 'portfolio_distribution_asset': 2,
 'portfolio_distribution_cash': 15435.479999999996,
 'reward': 0.001077619159850437,
 'strategy_returns': 0.0,
 'stock_price': 42336.17}

In [47]:
btc_dollar_val_data_subset = BTC_DOLLAR_VAL_DATA[['date', 'close']][9:].copy()
# calculo los retornos del benchmark

btc_dollar_val_data_subset['BTC Buy&Hold'] = BTC_DOLLAR_VAL_DATA['close'].pct_change()
btc_dollar_val_data_subset.reset_index(inplace=True, drop=True)
btc_dollar_val_data_subset

date     close  BTC Buy&Hold
0      2024-01-01 01:15:00  42282.26      0.000161
1      2024-01-01 01:18:00  42336.17      0.001275
2      2024-01-01 01:33:00  42344.41      0.000195
3      2024-01-01 01:41:00  42387.02      0.001006
4      2024-01-01 01:45:00  42386.13     -0.000021
...                    ...       ...           ...
159959 2024-06-30 19:55:00  62741.92     -0.000027
159960 2024-06-30 19:56:00  62688.88     -0.000845
159961 2024-06-30 19:57:00  62706.69      0.000284
159962 2024-06-30 19:58:00  62670.13     -0.000583
159963 2024-06-30 19:59:00  62668.26     -0.000030

[159964 rows x 3 columns]

In [48]:
len(btc_dollar_val_data_subset), len(btc_dollar_real_action_taken)

(159964, 159963)

In [49]:
# las acciones predichas directamente las tengo que mapear
action_mapping = [-1, 0, 1]
mapped_actions = [action_mapping[index] for index in btc_dollar_actions]

predicted_actions_fixed = [0]
real_actions_fixed = [0]
predicted_actions_fixed.extend(mapped_actions)
real_actions_fixed.extend(btc_dollar_real_action_taken)

btc_dollar_val_data_subset['predicted_actions'] = predicted_actions_fixed
btc_dollar_val_data_subset['real_actions_taken'] = real_actions_fixed

In [50]:
btc_dollar_val_data_subset['BTC_pred_actions_returns'] = calculate_returns(btc_dollar_val_data_subset,'predicted_actions')
btc_dollar_val_data_subset['BTC_real_actions_returns'] = calculate_returns(btc_dollar_val_data_subset,'real_actions_taken')

In [51]:
btc_dollar_val_data_subset.to_parquet('../04_testing/BTC_dollar_returns.parquet')

# SPY Original

In [25]:
SPY_original_model = PPO.load("ppo_SPY_original.zip")

In [62]:
SPY_ORIG_VAL_DATA = pd.read_parquet(r'C:\Users\adelapuente\Desktop\math_tfm\02_training_data\SPY_original_processed_out_of_sample.parquet')

In [63]:
SPY_ORIG_VAL_DATA.tail()

date  feature_open  feature_high  feature_low  \
662349 2024-06-28 15:56:00      0.983312      0.983531     0.982631   
662350 2024-06-28 15:57:00      0.982527      0.983270     0.982719   
662351 2024-06-28 15:58:00      0.983225      0.983517     0.982864   
662352 2024-06-28 15:59:00      0.982687      0.983037     0.981701   
662353 2024-06-28 16:00:00      0.982105      0.983648     0.981817   

        feature_close  feature_SMA_20  feature_SMA_50  feature_EMA_14  \
662349       0.982587        0.985349        0.985377        0.985162   
662350       0.983255        0.985373        0.985355        0.985051   
662351       0.982732        0.985335        0.985331        0.984885   
662352       0.982122        0.985273        0.985282        0.984660   
662353       0.982994        0.985225        0.985259        0.984581   

        feature_BBL_20_2.0  feature_BBM_20_2.0  feature_BBU_20_2.0  \
662349            0.984840            0.985349            0.984125   
662350            0.984935            0.985373            0.984078   
662351            0.984799            0.985335            0.984140   
662352            0.984547            0.985273            0.984270   
662353            0.984431            0.985225            0.984291   

        feature_BBB_20_2.0  feature_BBP_20_2.0  feature_RSI  feature_MACD  \
662349            0.011257            0.288262     0.404310      0.586870   
662350            0.010835            0.360657     0.451796      0.584587   
662351            0.011424            0.310175     0.423353      0.581320   
662352            0.012557            0.268076     0.392321      0.577068   
662353            0.012963            0.371647     0.453904      0.576366   

        feature_MACD_Signal  feature_MACD_Diff  feature_ATR  feature_CCI  \
662349             0.598553           0.651926     0.040217     0.397185   
662350             0.596085           0.651607     0.040622     0.404381   
662351             0.593351           0.649800     0.041290     0.405224   
662352             0.590173           0.646801     0.043861     0.371257   
662353             0.587468           0.650000     0.047660     0.414386   

         close  
662349  544.25  
662350  544.48  
662351  544.30  
662352  544.09  
662353  544.39

In [27]:
spy_orig_obs, spy_orig_rewards, spy_orig_infos, spy_orig_actions, spy_orig_real_action_taken = model_predict(SPY_original_model, SPY_ORIG_VAL_DATA)

BUYING --> 	price:475.15 | 	cost: 99781.50 | port: 100000.00 | port-1: 100000.00
SELLING --> 	price:475.15 | 	profit: 99781.50 | port: 100000.00 | port-1: 100000.00
BUYING --> 	price:472.68 | 	cost: 99735.69 | port: 100000.00 | port-1: 100000.00
SELLING --> 	price:471.85 | 	profit: 99560.35 | port: 99824.66 | port-1: 99820.44
BUYING --> 	price:471.81 | 	cost: 99550.85 | port: 99824.66 | port-1: 99824.66
SELLING --> 	price:472.25 | 	profit: 99643.70 | port: 99917.50 | port-1: 99897.45
BUYING --> 	price:472.08 | 	cost: 99608.88 | port: 99917.50 | port-1: 99917.50
SELLING --> 	price:472.11 | 	profit: 99614.15 | port: 99922.77 | port-1: 99871.08
BUYING --> 	price:471.97 | 	cost: 99585.67 | port: 99922.77 | port-1: 99922.77
SELLING --> 	price:471.97 | 	profit: 99585.67 | port: 99922.77 | port-1: 99903.78
BUYING --> 	price:472.18 | 	cost: 99630.19 | port: 99922.77 | port-1: 99922.77
SELLING --> 	price:472.19 | 	profit: 99632.09 | port: 99924.67 | port-1: 99966.87
BUYING --> 	price:472.32 | 	

In [28]:
spy_orig_infos[0]

{'idx': 10,
 'step': 1,
 'date': 611534,
 'agent_action': -1,
 'real_action_taken': 0,
 'portfolio_exposition': 0.0,
 'data_date': Timestamp('2024-01-01 09:40:00'),
 'data_close': 475.15,
 'portfolio_valuation': 100000.0,
 'portfolio_distribution_asset': 0,
 'portfolio_distribution_cash': 100000.0,
 'reward': -0.01,
 'strategy_returns': 0.0,
 'stock_price': 475.15}

In [64]:
spy_orig_val_data_subset = SPY_ORIG_VAL_DATA[['date', 'close']][9:].copy()
# calculo los retornos del benchmark

spy_orig_val_data_subset['SPY Buy&Hold'] = SPY_ORIG_VAL_DATA['close'].pct_change()
spy_orig_val_data_subset.reset_index(inplace=True, drop=True)
spy_orig_val_data_subset

date   close  SPY Buy&Hold
0     2024-01-01 09:39:00  475.15      0.000000
1     2024-01-01 09:40:00  475.15      0.000000
2     2024-01-01 09:41:00  475.15      0.000000
3     2024-01-01 09:42:00  475.15      0.000000
4     2024-01-01 09:43:00  475.15      0.000000
...                   ...     ...           ...
49324 2024-06-28 15:56:00  544.25     -0.000533
49325 2024-06-28 15:57:00  544.48      0.000423
49326 2024-06-28 15:58:00  544.30     -0.000331
49327 2024-06-28 15:59:00  544.09     -0.000386
49328 2024-06-28 16:00:00  544.39      0.000551

[49329 rows x 3 columns]

In [65]:
spy_orig_val_data_subset.tail(5)

date   close  SPY Buy&Hold
49324 2024-06-28 15:56:00  544.25     -0.000533
49325 2024-06-28 15:57:00  544.48      0.000423
49326 2024-06-28 15:58:00  544.30     -0.000331
49327 2024-06-28 15:59:00  544.09     -0.000386
49328 2024-06-28 16:00:00  544.39      0.000551

In [30]:
len(spy_orig_val_data_subset), len(spy_orig_real_action_taken)

(49329, 49328)

In [31]:
# las acciones predichas directamente las tengo que mapear
action_mapping = [-1, 0, 1]
mapped_actions = [action_mapping[index] for index in spy_orig_actions]

predicted_actions_fixed = [0]
real_actions_fixed = [0]
predicted_actions_fixed.extend(mapped_actions)
real_actions_fixed.extend(spy_orig_real_action_taken)

spy_orig_val_data_subset['predicted_actions'] = predicted_actions_fixed
spy_orig_val_data_subset['real_actions_taken'] = real_actions_fixed

In [32]:
spy_orig_val_data_subset['SPY_pred_actions_returns'] = calculate_returns(spy_orig_val_data_subset,'predicted_actions')
spy_orig_val_data_subset['SPY_real_actions_returns'] = calculate_returns(spy_orig_val_data_subset,'real_actions_taken')

In [33]:
spy_orig_val_data_subset.to_parquet('../04_testing/SPY_original_returns.parquet')

# SPY VOLUME

In [35]:
SPY_volume_model = PPO.load("ppo_SPY_volume.zip")

In [36]:
SPY_VOLUME_VAL_DATA = pd.read_parquet(r'C:\Users\adelapuente\Desktop\math_tfm\02_training_data\SPY_volume_processed_out_of_sample.parquet')

In [42]:
spy_volume_obs, spy_volume_rewards, spy_volume_infos, spy_volume_actions, spy_volume_real_action_taken = model_predict(SPY_original_model, SPY_VOLUME_VAL_DATA)

SELLING --> 	price:475.15 | 	profit: 99781.50 | port: 100000.00 | port-1: 100000.00
BUYING --> 	price:475.15 | 	cost: 99781.50 | port: 100000.00 | port-1: 100000.00
SELLING --> 	price:475.15 | 	profit: 99781.50 | port: 100000.00 | port-1: 100000.00
BUYING --> 	price:475.15 | 	cost: 99781.50 | port: 100000.00 | port-1: 100000.00
SELLING --> 	price:471.77 | 	profit: 99071.70 | port: 99290.20 | port-1: 99321.70
BUYING --> 	price:473.19 | 	cost: 98896.71 | port: 99290.20 | port-1: 99290.20
SELLING --> 	price:473.40 | 	profit: 98940.60 | port: 99334.09 | port-1: 99290.20
BUYING --> 	price:472.68 | 	cost: 99262.80 | port: 99334.09 | port-1: 99334.09
SELLING --> 	price:472.66 | 	profit: 99258.60 | port: 99329.89 | port-1: 99347.74
BUYING --> 	price:472.03 | 	cost: 99126.30 | port: 99329.89 | port-1: 99329.89
SELLING --> 	price:471.46 | 	profit: 99006.60 | port: 99210.19 | port-1: 99230.14
BUYING --> 	price:470.64 | 	cost: 98834.40 | port: 99210.19 | port-1: 99210.19
SELLING --> 	price:471.93 

In [43]:
spy_volume_infos[0]

{'idx': 10,
 'step': 1,
 'date': 51643,
 'agent_action': -1,
 'real_action_taken': 0,
 'portfolio_exposition': 0.0,
 'data_date': Timestamp('2024-01-01 10:13:00'),
 'data_close': 475.15,
 'portfolio_valuation': 100000.0,
 'portfolio_distribution_asset': 0,
 'portfolio_distribution_cash': 100000.0,
 'reward': -0.01,
 'strategy_returns': 0.0,
 'stock_price': 475.15}

In [44]:
spy_volume_val_data_subset = SPY_VOLUME_VAL_DATA[['date', 'close']][9:].copy()
# calculo los retornos del benchmark

spy_volume_val_data_subset['SPY Buy&Hold'] = SPY_VOLUME_VAL_DATA['close'].pct_change()
spy_volume_val_data_subset.reset_index(inplace=True, drop=True)
spy_volume_val_data_subset

date   close  SPY Buy&Hold
0    2024-01-01 10:09:00  475.15      0.000000
1    2024-01-01 10:13:00  475.15      0.000000
2    2024-01-01 10:17:00  475.15      0.000000
3    2024-01-01 10:21:00  475.15      0.000000
4    2024-01-01 10:25:00  475.15      0.000000
...                  ...     ...           ...
3468 2024-06-28 15:56:00  544.25     -0.000533
3469 2024-06-28 15:57:00  544.48      0.000423
3470 2024-06-28 15:58:00  544.30     -0.000331
3471 2024-06-28 15:59:00  544.09     -0.000386
3472 2024-06-28 16:00:00  544.39      0.000551

[3473 rows x 3 columns]

In [45]:
len(spy_volume_val_data_subset), len(spy_volume_real_action_taken)

(3473, 3472)

In [46]:
# las acciones predichas directamente las tengo que mapear
action_mapping = [-1, 0, 1]
mapped_actions = [action_mapping[index] for index in spy_volume_actions]

predicted_actions_fixed = [0]
real_actions_fixed = [0]
predicted_actions_fixed.extend(mapped_actions)
real_actions_fixed.extend(spy_volume_real_action_taken)

spy_volume_val_data_subset['predicted_actions'] = predicted_actions_fixed
spy_volume_val_data_subset['real_actions_taken'] = real_actions_fixed

In [47]:
spy_volume_val_data_subset['SPY_pred_actions_returns'] = calculate_returns(spy_volume_val_data_subset,'predicted_actions')
spy_volume_val_data_subset['SPY_real_actions_returns'] = calculate_returns(spy_volume_val_data_subset,'real_actions_taken')

In [48]:
spy_volume_val_data_subset.to_parquet('../04_testing/SPY_volume_returns.parquet')

# SPY DOLLAR

In [49]:
SPY_dollar_model = PPO.load("ppo_SPY_dollar.zip")

In [50]:
SPY_DOLLAR_VAL_DATA = pd.read_parquet(r'C:\Users\adelapuente\Desktop\math_tfm\02_training_data\SPY_dollar_processed_out_of_sample.parquet')

In [51]:
spy_dollar_obs, spy_dollar_rewards, spy_dollar_infos, spy_dollar_actions, spy_dollar_real_action_taken = model_predict(SPY_original_model, SPY_DOLLAR_VAL_DATA)

SELLING --> 	price:475.15 | 	profit: 99781.50 | port: 100000.00 | port-1: 100000.00
BUYING --> 	price:475.15 | 	cost: 99781.50 | port: 100000.00 | port-1: 100000.00
SELLING --> 	price:472.65 | 	profit: 99256.50 | port: 99475.00 | port-1: 99483.40
BUYING --> 	price:472.47 | 	cost: 99218.70 | port: 99475.00 | port-1: 99475.00
SELLING --> 	price:471.76 | 	profit: 99069.60 | port: 99325.90 | port-1: 99367.90
BUYING --> 	price:472.19 | 	cost: 99159.90 | port: 99325.90 | port-1: 99325.90
SELLING --> 	price:472.24 | 	profit: 99170.40 | port: 99336.40 | port-1: 99325.90
BUYING --> 	price:472.33 | 	cost: 99189.30 | port: 99336.40 | port-1: 99336.40
SELLING --> 	price:473.30 | 	profit: 99393.00 | port: 99540.10 | port-1: 99489.70
BUYING --> 	price:473.23 | 	cost: 99378.30 | port: 99540.10 | port-1: 99540.10
SELLING --> 	price:472.91 | 	profit: 99311.10 | port: 99472.90 | port-1: 99540.10
BUYING --> 	price:473.29 | 	cost: 99390.90 | port: 99472.90 | port-1: 99472.90
SELLING --> 	price:472.83 | 	p

In [52]:
spy_dollar_infos[0]

{'idx': 10,
 'step': 1,
 'date': 76135,
 'agent_action': -1,
 'real_action_taken': 0,
 'portfolio_exposition': 0.0,
 'data_date': Timestamp('2024-01-01 09:51:00'),
 'data_close': 475.15,
 'portfolio_valuation': 100000.0,
 'portfolio_distribution_asset': 0,
 'portfolio_distribution_cash': 100000.0,
 'reward': -0.01,
 'strategy_returns': 0.0,
 'stock_price': 475.15}

In [53]:
spy_dollar_val_data_subset = SPY_DOLLAR_VAL_DATA[['date', 'close']][9:].copy()
# calculo los retornos del benchmark

spy_dollar_val_data_subset['SPY Buy&Hold'] = SPY_DOLLAR_VAL_DATA['close'].pct_change()
spy_dollar_val_data_subset.reset_index(inplace=True, drop=True)
spy_dollar_val_data_subset

date   close  SPY Buy&Hold
0    2024-01-01 09:49:00  475.15      0.000000
1    2024-01-01 09:51:00  475.15      0.000000
2    2024-01-01 09:53:00  475.15      0.000000
3    2024-01-01 09:55:00  475.15      0.000000
4    2024-01-01 09:57:00  475.15      0.000000
...                  ...     ...           ...
8382 2024-06-28 15:56:00  544.25     -0.000533
8383 2024-06-28 15:57:00  544.48      0.000423
8384 2024-06-28 15:58:00  544.30     -0.000331
8385 2024-06-28 15:59:00  544.09     -0.000386
8386 2024-06-28 16:00:00  544.39      0.000551

[8387 rows x 3 columns]

In [54]:
len(spy_dollar_val_data_subset), len(spy_dollar_real_action_taken)

(8387, 8386)

In [55]:
# las acciones predichas directamente las tengo que mapear
action_mapping = [-1, 0, 1]
mapped_actions = [action_mapping[index] for index in spy_dollar_actions]

predicted_actions_fixed = [0]
real_actions_fixed = [0]
predicted_actions_fixed.extend(mapped_actions)
real_actions_fixed.extend(spy_dollar_real_action_taken)

spy_dollar_val_data_subset['predicted_actions'] = predicted_actions_fixed
spy_dollar_val_data_subset['real_actions_taken'] = real_actions_fixed

In [56]:
spy_dollar_val_data_subset['SPY_pred_actions_returns'] = calculate_returns(spy_dollar_val_data_subset,'predicted_actions')
spy_dollar_val_data_subset['SPY_real_actions_returns'] = calculate_returns(spy_dollar_val_data_subset,'real_actions_taken')

In [57]:
spy_dollar_val_data_subset.to_parquet('../04_testing/SPY_dollar_returns.parquet')